In [3]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
import mysql.connector

In [ ]:
triples_repodb = pd.read_csv("./Data/Input/Drug Repurposing/triples_filter_repodb_final.tsv", sep='\,')
triples_repodb = triples_repodb.drop(columns=['Unnamed: 0'])

In [6]:
drug_gen = pd.read_csv('./Data/Input/DISNET/drug_gen.tsv', sep='\t')
drug_gen = drug_gen.drop(["Unnamed: 0"],axis=1)

In [8]:
tri_gen_target= triples_repodb.merge(drug_gen, left_on = "drug",right_on = "drug_id",how= "inner")

In [10]:
tri_gen_target = tri_gen_target.drop(["drug"],axis=1)

In [16]:
tri_gen_target = tri_gen_target.rename(columns={"disease1": "disease_id"})

In [19]:
tri_gen_target = tri_gen_target.rename(columns={"disease2": "disease_id_new"})

In [12]:
dis_gen = pd.read_csv('./Data/Input/DISNET/dis_gen.tsv', sep='\t')
dis_gen = dis_gen.drop(["Unnamed: 0"],axis=1)

In [21]:
dis_gen_new = dis_gen.rename(columns={"disease_id": "disease2"})

In [17]:
disease_gen_one = tri_gen_target.merge(dis_gen, on = ["gene_id","disease_id"],how="inner")

In [22]:
disease_gen_one = disease_gen_one.merge(dis_gen_new, on = ["gene_id","disease2"],how="inner")

In [53]:
triples_final_drege = disease_gen_one.drop(["score_x","score_y"],axis=1)

In [54]:
triples_final_drege = triples_final_drege.drop_duplicates()

In [55]:
triples_final_drege = triples_final_drege.drop(["gene_id"],axis=1)

In [56]:
triples_final_drege = triples_final_drege.drop_duplicates()

# CSBJ

In [37]:
triplets_csbj = pd.read_excel("./Data/Input/DISNET/triplets_chembl_disnet.xlsx",engine='openpyxl')
triplets_csbj =triplets_csbj.drop(["Unnamed: 0"],axis=1)

In [40]:
tri_gen_target_csbj= triplets_csbj.merge(drug_gen, on = "drug_id",how= "inner")

In [42]:
tri_gen_target_csbj = tri_gen_target_csbj.rename(columns={"Original Condition CUI": "disease_id"})

In [43]:
disease_gen_one_csbj = tri_gen_target_csbj.merge(dis_gen, on = ["gene_id","disease_id"],how="inner")

In [45]:
dis_gen_new = dis_gen.rename(columns={"disease_id": "New Condition CUI"})

In [48]:
disease_gen_one_csbj_twounion = disease_gen_one_csbj.merge(dis_gen_new, on = ["gene_id","New Condition CUI"],how="inner")

In [50]:
triplets_csbj_drege = disease_gen_one_csbj_twounion[["disease_id","New Condition CUI","drug_id"]]

In [65]:
triplets_csbj_drege =triplets_csbj_drege.drop_duplicates()

# FINAL TRIPLES DREGE

In [61]:
triples_final_drege = triples_final_drege.rename(columns={"disease2": "New Condition CUI"})

In [67]:
triples_final_drege_repo_csbj = pd.concat([triplets_csbj_drege,triples_final_drege])

In [70]:
triples_final_drege_repo_csbj = triples_final_drege_repo_csbj.drop_duplicates()

In [72]:
triples_final_drege_repo_csbj.to_excel("triples_final_drege_repo_csbj.xlsx")